## Obtaining data for public transport in London

In [4]:
# The code was removed by Watson Studio for sharing.

FID  OBJECTID           NAME  EASTING  NORTHING             LINES  \
0    0        78         Temple   530959    180803  District, Circle   
1    1        79    Blackfriars   531694    180893  District, Circle   
2    2        80  Mansion House   532354    180932  District, Circle   
3    3        81  Cannon Street   532611    180900  District, Circle   
4    4        82       Monument   532912    180824  District, Circle   

              NETWORK  Zone         x          y  
0  London Underground     1 -0.112644  51.510474  
1  London Underground     1 -0.102020  51.511114  
2  London Underground     1 -0.092495  51.511306  
3  London Underground     1 -0.088801  51.510963  
4  London Underground     1 -0.084502  51.510209

In [5]:
df_lon.dropna(inplace=True)
df_lon.drop(['FID','OBJECTID','EASTING','NORTHING','LINES','NETWORK','Zone'],axis=1,inplace=True)

In [6]:
df_lon.rename(columns={'x':'Longitude','y':'Latitude'},inplace=True)

### Searching for venues near the London public transport access points

In [7]:
import requests
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [8]:
LIMIT = 100

In [9]:
CLIENT_ID='YVQPS55HY0S0MPSXDHA3PNYBWQS4CIVDIWDELIDO4NDYBWHP'
CLIENT_SECRET='1PONAFT43O0DLKO5SC4MSTSYTYZZEOPTSHHJAQNKMNLTPH3J'
VERSION=20180605

In [10]:
df_venues = getNearbyVenues(names = df_lon['NAME'],latitudes = df_lon['Latitude'],longitudes = df_lon['Longitude'])

Temple
Blackfriars
Mansion House
Cannon Street
Monument
Tower Hill
Aldgate
Liverpool Street
Moorgate
Barbican
Farringdon
King's Cross St. Pancras
Euston Square
Great Portland Street
Baker Street
Edgware Road (Circle Line)
Paddington
Bayswater
High Street Kensington
Gloucester Road
South Kensington
Victoria
Pimlico
Warren Street
Queensway
Hyde Park Corner
Knightsbridge
Leicester Square
Covent Garden
Russell Square
Earl's Court
Notting Hill Gate
Lancaster Gate
Marble Arch
Bond Street
Bank
Oxford Circus
Holborn
Chancery Lane
St. Paul's
Paddington
Embankment
Westminster
Euston
Waterloo
Green Park
Paddington (H&C Line)
Piccadilly Circus
Charing Cross
Lambeth North
Edgware Road (Bakerloo)
Marylebone
Regent's Park
Sloane Square
St. James's Park
Goodge Street
Tottenham Court Road
Borough
Old Street
Angel
Aldgate East
Southwark
London Bridge
East Putney
Putney Bridge
Parsons Green
White City
Shepherd's Bush
Holland Park
Brixton
Vauxhall
Highbury & Islington
Caledonian Road
Holloway Road
Arsenal

### Removing venues other than pubs from the dataset

In [11]:
df_venues.head()
df_venues.to_csv('Venues.csv')

In [12]:
df_venues['Pubs'] = [1 if x =='Pub' else 0 for x in df_venues['Venue Category']]

In [13]:
df_pubs = df_venues[df_venues['Pubs'] == 1]

In [14]:
df_pubs.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
3        Temple              51.510474               -0.112644   
6        Temple              51.510474               -0.112644   
8        Temple              51.510474               -0.112644   
32       Temple              51.510474               -0.112644   
36       Temple              51.510474               -0.112644   

                      Venue  Venue Latitude  Venue Longitude Venue Category  \
3         Temple Brew House       51.512940        -0.113029            Pub   
6         The Edgar Wallace       51.512585        -0.112819            Pub   
8            The Understudy       51.507725        -0.113724            Pub   
32      The Cheshire Cheese       51.512531        -0.113178            Pub   
36  The Old Bank of England       51.513870        -0.111491            Pub   

    Pubs  
3      1  
6      1  
8      1  
32     1  
36     1

In [15]:
df_pubs.drop(['Neighborhood Latitude','Neighborhood Longitude','Venue Category'],axis=1,inplace=True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [16]:
df_pubs.reset_index(inplace=True)

In [17]:
df_pubs.head()

index Neighborhood                    Venue  Venue Latitude  \
0      3       Temple        Temple Brew House       51.512940   
1      6       Temple        The Edgar Wallace       51.512585   
2      8       Temple           The Understudy       51.507725   
3     32       Temple      The Cheshire Cheese       51.512531   
4     36       Temple  The Old Bank of England       51.513870   

   Venue Longitude  Pubs  
0        -0.113029     1  
1        -0.112819     1  
2        -0.113724     1  
3        -0.113178     1  
4        -0.111491     1

### Creating a map with all pubs obtained from Foursquare

In [20]:
!conda install -c conda-forge folium=0.5.0
import folium

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    branca-0.4.1               |             py_0          26 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    ------------------------------------------------------------
                       

In [21]:
map_london = folium.Map(location=[51.51,-0.11], zoom_start=12)

# add markers to map
for lat, lng, neighborhood, venue in zip(df_pubs['Venue Latitude'], df_pubs['Venue Longitude'], df_pubs['Neighborhood'], df_pubs['Venue']):
    label = '{}, {}'.format(venue,neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

### Adding the data for public transport to the map

In [22]:

body = client_843c80ec5aab45029a5e149891fbb8df.get_object(Bucket='coursera-donotdelete-pr-xuctsznipu8kkf',Key='Book2.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data = pd.read_csv(body)
df_data.head(11)


FID  OBJECTID              NAME  EASTING  NORTHING  \
0     0        78            Temple   530959    180803   
1     1        79       Blackfriars   531694    180893   
2     2        80     Mansion House   532354    180932   
3     3        81     Cannon Street   532611    180900   
4     4        82          Monument   532912    180824   
5     5        83        Tower Hill   533579    180755   
6     6        84           Aldgate   533613    181262   
7     7        85  Liverpool Street   533094    181567   
8     8        86          Moorgate   532668    181668   
9     9        87          Barbican   532004    181856   
10   10        88        Farringdon   531560    181874   

                                                LINES             NETWORK  \
0                                    District, Circle  London Underground   
1                                    District, Circle  London Underground   
2                                    District, Circle  London Underground   
3                                    District, Circle  London Underground   
4                                    District, Circle  London Underground   
5                                    District, Circle  London Underground   
6                                Metropolitan, Circle  London Underground   
7   Metropolitan, Central, Circle, Hammersmith & City  London Underground   
8   Metropolitan, Northern, Circle, Hammersmith & ...  London Underground   
9            Metropolitan, Circle, Hammersmith & City  London Underground   
10           Metropolitan, Circle, Hammersmith & City  London Underground   

    Zone         x          y  
0      1 -0.112644  51.510474  
1      1 -0.102020  51.511114  
2      1 -0.092495  51.511306  
3      1 -0.088801  51.510963  
4      1 -0.084502  51.510209  
5      1 -0.074914  51.509434  
6      1 -0.074236  51.513982  
7      1 -0.081601  51.516842  
8      1 -0.087700  51.517853  
9      1 -0.097190  51.519699  
10     1 -0.103582  51.519961

In [23]:
for lat, lng, network, name in zip(df_data['y'], df_data['x'], df_data['NETWORK'], df_data['NAME']):
    label = '{}, {}'.format(name,network)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        parse_html=False).add_to(map_london) 
map_london

## Using clustering to select suitable areas for a new pub

In [24]:
df_pubs['Neighborhood'].value_counts()

Paddington                  19
Richmond                    12
Aldgate East                11
Holborn                      9
Ravenscourt Park             9
Borough                      9
Angel                        9
Camden Town                  9
Chancery Lane                8
Clapham Common               8
Hammersmith (H&C Line)       7
Highbury & Islington         7
Kentish Town                 7
Kennington                   7
Stratford                    6
Southwark                    6
Fulham Broadway              6
Ealing Broadway              6
Wimbledon                    6
Temple                       6
Chiswick Park                6
Farringdon                   6
Chalk Farm                   5
Turnham Green                5
Bethnal Green                5
Putney Bridge                5
Paddington (H&C Line)        5
Notting Hill Gate            5
Bayswater                    5
Leytonstone                  5
                            ..
Tottenham Hale               1
Caledoni

In [25]:
from sklearn.cluster import KMeans
df_pubs.columns

Index(['index', 'Neighborhood', 'Venue', 'Venue Latitude', 'Venue Longitude',
       'Pubs'],
      dtype='object')

In [26]:
df_loc=df_pubs.drop(['Venue','Neighborhood','index'],axis=1)
df_loc.head()

Venue Latitude  Venue Longitude  Pubs
0       51.512940        -0.113029     1
1       51.512585        -0.112819     1
2       51.507725        -0.113724     1
3       51.512531        -0.113178     1
4       51.513870        -0.111491     1

In [27]:
kmeans = KMeans(n_clusters=4, random_state=0).fit(df_loc)

In [28]:
kmeans.labels_

array([3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1, 3, 3, 3, 3, 3, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 3, 3, 3, 3, 1, 1, 1,

In [29]:
df_pubs.insert(0, 'Cluster_Labels', kmeans.labels_)

In [30]:
import numpy as np
import matplotlib.cm as cm
import matplotlib.colors as colors

In [31]:
map_clusters = folium.Map(location=[51.51,-0.11], zoom_start=11)

# set color scheme for the clusters
x = np.arange(4)
ys = [i + x + (i*x)**2 for i in range(4)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_pubs['Venue Latitude'], df_pubs['Venue Longitude'], df_pubs['Neighborhood'], df_pubs['Cluster_Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters


In [32]:
df_pubs.reset_index(drop=True)
df_data.reset_index(drop=True)

FID  OBJECTID                        NAME  EASTING  NORTHING  \
0      0        78                      Temple   530959    180803   
1      1        79                 Blackfriars   531694    180893   
2      2        80               Mansion House   532354    180932   
3      3        81               Cannon Street   532611    180900   
4      4        82                    Monument   532912    180824   
5      5        83                  Tower Hill   533579    180755   
6      6        84                     Aldgate   533613    181262   
7      7        85            Liverpool Street   533094    181567   
8      8        86                    Moorgate   532668    181668   
9      9        87                    Barbican   532004    181856   
10    10        88                  Farringdon   531560    181874   
11    11        89    King's Cross St. Pancras   530175    182875   
12    12        90               Euston Square   529417    182393   
13    13        91       Great Portland Street   528838    182180   
14    14        92                Baker Street   527955    182064   
15    15        93  Edgware Road (Circle Line)   527220    181697   
16    16        94                  Paddington   526704    181198   
17    17        95                   Bayswater   525843    180823   
18    18        96      High Street Kensington   525578    179494   
19    19        97             Gloucester Road   526183    178846   
20    20        98            South Kensington   526918    178820   
21    21       110                    Victoria   528999    179130   
22    22       112                     Pimlico   529671    178333   
23    23       114               Warren Street   529249    182266   
24    24       119                   Queensway   525903    180594   
25    25        14            Hyde Park Corner   528213    179817   
26    26        15               Knightsbridge   527710    179636   
27    27        16            Leicester Square   529980    180824   
28    28        17               Covent Garden   530251    181025   
29    29        18              Russell Square   530229    182128   
..   ...       ...                         ...      ...       ...   
449  449       154                   Upminster   556108    186859   
450  450       179                   Hatch End   513054    191323   
451  451       390                     Romford   551350    188463   
452  452       391                  Gidea Park   552906    189285   
453  453       392                 Harold Wood   554777    190568   
454  454       420                 Gravel Hill   536373    163537   
455  455       421           Addington Village   537066    163744   
456  456       422               New Addington   538198    162244   
457  457       423          King Henry's Drive   537977    162560   
458  458       424                    Fieldway   537684    163173   
459  459       321                 Chorleywood   502581    196095   
460  460       323               Rickmansworth   505716    194601   
461  461       324                   Moor Park   508606    193503   
462  462       326                     Croxley   507909    195403   
463  463       327                     Watford   509569    196596   
464  464       152             Theobalds Grove   535936    201110   
465  465       169             Carpenders Park   511833    193398   
466  466       320          Chalfont & Latimer   499634    197564   
467  467       134                    Cheshunt   536644    202316   
468  468       360         Watford High Street   511326    196075   
469  469       365            Watford Junction   511021    197351   
470  470       366                      Bushey   511823    195237   
471  471       322                     Chesham   496079    201633   
472  472       284                    Amersham   496372    198181   
473  473       137                     Clapton   534775    186528   
474  474       381              Crystal Palace   534111    170555   
475

In [33]:
publist=df_pubs['Neighborhood'].tolist()

In [34]:
publist=list(set(publist))

In [35]:
publist

['Marble Arch',
 'Aldgate',
 'Baker Street',
 'Covent Garden',
 'Roding Valley',
 'Cannon Street',
 'Preston Road',
 "Earl's Court",
 "King's Cross St. Pancras",
 'Golders Green',
 'Ladbroke Grove',
 'Wanstead',
 'Stratford',
 'Kennington',
 'Willesden Green',
 'Westbourne Park',
 'Marylebone',
 'Highbury & Islington',
 'West Brompton',
 'Moorgate',
 'Chalk Farm',
 'Upminster',
 'Maida Vale',
 'Kingsbury',
 'Dagenham Heathway',
 'London Bridge',
 'Lancaster Gate',
 'South Harrow',
 'Bond Street',
 'South Kenton',
 'Ealing Broadway',
 'Oval',
 'Hammersmith (Dist&Picc Line)',
 'Turnham Green',
 'Hatton Cross',
 'Edgware Road (Bakerloo)',
 'Angel',
 'Mornington Crescent',
 'South Ealing',
 'Totteridge & Whetstone',
 'Finchley Central',
 'Victoria',
 'Bank',
 'Snaresbrook',
 'Tooting Broadway',
 'Heathrow Terminals 1-2-3',
 'Kilburn Park',
 'Richmond',
 'Chiswick Park',
 'Russell Square',
 'Buckhurst Hill',
 'Kilburn',
 'South Ruislip',
 'Stamford Brook',
 'Putney Bridge',
 'Holland Park',

In [41]:
trlist=df_data['NAME'].tolist()

In [43]:
spots=list(set(trlist) - set(publist))

In [44]:
spots

['South Kensington',
 'Kilburn High Road',
 'Hatch End',
 'White City',
 'Rotherhithe',
 'Enfield Town',
 'Manor Park',
 'Canning Town',
 'Cheshunt',
 'Belgrave Walk',
 'Hackney Central',
 'LANGDON PARK - DLR',
 'Edmondton Green',
 'Canons Park',
 'MUDCHUTE - DLR',
 'Crouch Hill',
 'Highams Park',
 'ELVERSON ROAD - DLR',
 'Upper Holloway',
 'LIMEHOUSE - DLR',
 'Harrington Road',
 'ISLAND GARDENS - DLR',
 'Loughton',
 'Clapham Junction',
 'South Hampstead',
 'WESTFERRY - DLR',
 'Denmark Hill',
 'WOOLWICH ARSENAL - DLR',
 'Brondesbury Park',
 'West Ham',
 'Queens Road Peckham',
 'Latimer Road',
 'Wimbledon (Tramlink)',
 'Hampstead Heath',
 'Harold Wood',
 'Waddon Marsh',
 'Chalfont & Latimer',
 'Walthamstow Wood Street',
 'London Fields',
 'North Wembley',
 'Watford High Street',
 'Harringay Green Lanes',
 'Centrale',
 'Harrow & Wealdstone',
 'Hanger Lane',
 'CUSTOM HOUSE - DLR',
 'Sudbury Hill',
 'Shoreditch High Street',
 'Dagenham East',
 'Woodside',
 'Rectory Road',
 'PONTOON DOCK - 

In [49]:
df_spots=df_data[df_data['NAME'].isin(spots)]

In [51]:
df_spots.reset_index()

index  FID  OBJECTID                    NAME  EASTING  NORTHING  \
0        2    2        80           Mansion House   532354    180932   
1        5    5        83              Tower Hill   533579    180755   
2       20   20        98        South Kensington   526918    178820   
3       26   26        15           Knightsbridge   527710    179636   
4       39   39        51              St. Paul's   532108    181274   
5       45   45       206              Green Park   529007    180295   
6       55   55       308           Goodge Street   529537    181837   
7       56   56       309    Tottenham Court Road   529815    181382   
8       60   60       339  Shoreditch High Street   533555    182248   
9       66   66       470     TOWER GATEWAY - DLR   533706    180834   
10      67   67       473              BANK - DLR   532709    181114   
11      72   72       105              White City   523308    180748   
12      84   84        33            Latimer Road   523763    180898   
13      91   91       191             Rotherhithe   535299    179811   
14     121  121       334               Wood Lane   523374    180519   
15     122  122       336            Canada Water   535475    179472   
16     123  123       337                Shadwell   534932    180932   
17     125  125       340                  Hoxton   533576    183148   
18     126  126       341              Haggerston   533560    183992   
19     127  127       342        Dalston Junction   533578    184692   
20     128  128       343               New Cross   536751    177109   
21     129  129       344                Brockley   536431    175789   
22     139  139       290            Canada Water   535457    179467   
23     141  141       292            Canary Wharf   537677    180140   
24     143  143       133         Cambridge Heath   534856    183270   
25     144  144       136     Clapham High Street   529804    175717   
26     145  145       138            Denmark Hill   532792    176078   
27     146  146       142           Hackney Downs   534551    185122   
28     147  147       145           London Fields   534775    184246   
29     148  148       146             Peckham Rye   534222    176360   
..     ...  ...       ...                     ...      ...       ...   
234    439  439       268     Heathrow Terminal 4   508082    174430   
235    443  443       274                 Ruislip   509474    187004   
236    445  445       277         Northwood Hills   510308    190238   
237    446  446       140            Emerson Park   553962    187871   
238    447  447       149                 Romford   551387    188501   
239    448  448       153           Turkey Street   535121    198870   
240    450  450       179               Hatch End   513054    191323   
241    451  451       390                 Romford   551350    188463   
242    452  452       391              Gidea Park   552906    189285   
243    453  453       392             Harold Wood   554777    190568   
244    454  454       420             Gravel Hill   536373    163537   
245    455  455       421       Addington Village   537066    163744   
246    456  456       422           New Addington   538198    162244   
247    457  457       423      King Henry's Drive   537977    162560   
248    458  458       424                Fieldway   537684    163173   
249    463  463       327                 Watford   509569    196596   
250    464  464       152         Theobalds Grove   535936    201110   
251    465  465       169         Carpenders Park   511833    193398   
252    466  466       320      Chalfont & Latimer   499634    197564   
253    467  467       134                Cheshunt   536644    202316   
254    468  468       360     Watford High Street   511326    196075   
255    469  469       365        Watford Junction   511021    197351   
256    470  470       366                  Bushey   511823    195237   
257    472  472       284                Amer

In [52]:
for lat, lng, network, name in zip(df_spots['y'], df_spots['x'], df_spots['NETWORK'], df_spots['NAME']):
    label = '{}, {}'.format(name,network)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='white',
        parse_html=False).add_to(map_clusters)
map_clusters